<a id='0'></a>
# Part 1. Problem Definition

This problem is to design an automated trading solution for single stock trading. We model the stock trading process as a Markov Decision Process (MDP). We then formulate our trading goal as a maximization problem.

The algorithm is trained using Deep Reinforcement Learning (DRL) algorithms and the components of the reinforcement learning environment are:


* Action: 
* Reward function: 
* State: 
* Environment: 

<a id='1'></a>
# Part 2. Getting Started- Load Python Packages

<a id='1.1'></a>
## 2.1. Install all the packages

In [1]:
!pip install -r requirements.txt --user

  Cloning git://github.com/dvdpedros/pyfolio (to revision fix-extreme-drawdown) to c:\users\adega\appdata\local\temp\pip-req-build-nnk_hzx2


  Running command git clone -q git://github.com/dvdpedros/pyfolio 'C:\Users\adega\AppData\Local\Temp\pip-req-build-nnk_hzx2'
  Running command git checkout -b fix-extreme-drawdown --track origin/fix-extreme-drawdown
  Branch 'fix-extreme-drawdown' set up to track remote branch 'fix-extreme-drawdown' from 'origin'.
  Switched to a new branch 'fix-extreme-drawdown'


<a id='1.2'></a>
## 2.2. Import Packages

In [2]:
%load_ext autoreload
%autoreload 
import pandas as pd
from config import config
from dataset.download_dataset.cryptodownloader_binance import CryptoDownloader_binance
from preprocessing.preprocessors import FeatureEngineer
from preprocessing.data import data_split
from env.env_custom import CustomTradingEnv
from model.models import DRLAgent
from trade.backtest import BackTest
import warnings
warnings.filterwarnings("ignore")



C:\Users\adega\AppData\Roaming\Python\Python38\site-packages\pyfolio\pos.py:26: UserWarning: Module "zipline.assets" not found; multipliers will not be applied to position notionals.
  warnings.warn(


<a id='1.3'></a>
## 2.3 Create Folders

In [3]:
import os
download_data = False
if not os.path.exists(config.DATA_SAVE_DIR):
    os.makedirs(config.DATA_SAVE_DIR)
    download_data = True
if not os.path.exists(config.TRAINED_MODEL_DIR):
    os.makedirs("./" + config.TRAINED_MODEL_DIR)
if not os.path.exists(config.TENSORBOARD_LOG_DIR):
    os.makedirs(config.TENSORBOARD_LOG_DIR)
if not os.path.exists(config.RESULTS_DIR):
    os.makedirs(config.RESULTS_DIR)

<a id='2'></a>
# Part 3. Download Data

In [4]:
data_downloader = CryptoDownloader_binance(config.START_DATE, config.END_DATE, config.MULTIPLE_TICKER_8, config.DATA_SAVE_DIR, config.DATA_GRANULARITY)
if download_data:    
    data_downloader.download_data()
df = data_downloader.load()

Downloaded https://data.binance.vision/data/spot/monthly/klines/BTCUSDT/1h/BTCUSDT-1h-2020-01.zip
Downloaded https://data.binance.vision/data/spot/monthly/klines/ETHUSDT/1h/ETHUSDT-1h-2020-01.zip
Downloaded https://data.binance.vision/data/spot/monthly/klines/BNBUSDT/1h/BNBUSDT-1h-2020-01.zip
Downloaded https://data.binance.vision/data/spot/monthly/klines/ADAUSDT/1h/ADAUSDT-1h-2020-01.zip
Downloaded https://data.binance.vision/data/spot/monthly/klines/XRPUSDT/1h/XRPUSDT-1h-2020-01.zip
Downloaded https://data.binance.vision/data/spot/monthly/klines/DOGEUSDT/1h/DOGEUSDT-1h-2020-01.zip
Downloaded https://data.binance.vision/data/spot/monthly/klines/LINKUSDT/1h/LINKUSDT-1h-2020-01.zip
Downloaded https://data.binance.vision/data/spot/monthly/klines/LTCUSDT/1h/LTCUSDT-1h-2020-01.zip
Downloaded https://data.binance.vision/data/spot/monthly/klines/BTCUSDT/1h/BTCUSDT-1h-2020-02.zip
Downloaded https://data.binance.vision/data/spot/monthly/klines/ETHUSDT/1h/ETHUSDT-1h-2020-02.zip
Downloaded https

# Part 4: Preprocess Data

In [5]:
fe = FeatureEngineer(
                    use_technical_indicator=True,
                    use_turbulence=False,
                    user_defined_feature = True)

df = fe.preprocess_data(df)

Successfully added technical indicators
Successfully added user defined features


<a id='4'></a>
# Part 5. Design Environment
Considering the stochastic and interactive nature of the automated stock trading tasks, a financial task is modeled as a **Markov Decision Process (MDP)** problem. The training process involves observing stock price change, taking an action and reward's calculation to have the agent adjusting its strategy accordingly. By interacting with the environment, the trading agent will derive a trading strategy with the maximized rewards as time proceeds.

Our trading environments, based on OpenAI Gym framework, simulate live stock markets with real market data according to the principle of time-driven simulation.

The action space describes the allowed actions that the agent interacts with the environment. Normally, action a includes three actions: {-1, 0, 1}, where -1, 0, 1 represent selling, holding, and buying one share. Also, an action can be carried upon multiple shares. We use an action space {-k,…,-1, 0, 1, …, k}, where k denotes the number of shares to buy and -k denotes the number of shares to sell. For example, "Buy 10 shares of AAPL" or "Sell 10 shares of AAPL" are 10 or -10, respectively. The continuous action space needs to be normalized to [-1, 1], since the policy is defined on a Gaussian distribution, which needs to be normalized and symmetric.

## Training data split: 2020-01-01 to 2020-12-31

In [6]:
train = data_split(df, '2020-02-02','2020-12-31')

## Environment for Portfolio Allocation


In [7]:
stock_dimension = len(config.SINGLE_TICKER)
state_space = 1 + 2*stock_dimension + len(config.TECHNICAL_INDICATORS_LIST)*stock_dimension
print(f"Stock Dimension: {stock_dimension}, State Space: {state_space}")
features = config.TECHNICAL_INDICATORS_LIST + ["open", "close", 'high', 'low']
features += [f"{feature}_diff" for feature in features]

env_kwargs_singleticker = {
    "initial_amount": 1000000, 
    "technical_indicator_list": features, 
    "max_assets_amount_per_trade": 100, 
    "main_tickers": config.SINGLE_TICKER,
    "all_tickers": train.tic.unique(),
    "reward_scaling": 1e-4,
    "comission_value": 0.1,
    "discrete_actionspace":True
    
}

e_train_gym_singleticker = CustomTradingEnv(df = train, **env_kwargs_singleticker)

env_train_discreteactionspace, _ = e_train_gym_singleticker.get_sb_env()

Stock Dimension: 1, State Space: 21


In [8]:
stock_dimension = len(train.tic.unique())
state_space = stock_dimension
print(f"Stock Dimension: {stock_dimension}, State Space: {state_space}")
features = config.TECHNICAL_INDICATORS_LIST + ["open", "close", 'high', 'low']
features += [f"{feature}_diff" for feature in features]
features += [feature for feature in df.columns if feature.startswith("cov_")]

env_kwargs_multipleticker = {
    "initial_amount": 1000000, 
    "technical_indicator_list": features, 
    "max_assets_amount_per_trade": 100, 
    "main_tickers": train.tic.unique(),
    "all_tickers": train.tic.unique(),
    "reward_scaling": 1e-4,
    "comission_value": 0.01,
    "discrete_actionspace":False
    
}

e_train_gym_multipleticker = CustomTradingEnv(df = train, **env_kwargs_multipleticker)

env_train_continousactionspace, _ = e_train_gym_multipleticker.get_sb_env()

Stock Dimension: 8, State Space: 8


<a id='5'></a>
# Part 6: Implement DRL Algorithms

In [9]:
# initialize
agent_singleticker = DRLAgent(env = env_train_discreteactionspace)
agent_multipleticker = DRLAgent(env = env_train_continousactionspace)

### Model 1: **DQN**

In [12]:
model_dqn = agent_singleticker.get_model(model_name="dqn",model_kwargs=config.DQN_PARAMS)

Using cuda device


In [15]:
trained_dqn = agent_singleticker.train_model(model=model_dqn, 
                                tb_log_name='dqn',
                                total_timesteps=10000)

### Model 2: **A2C**


In [16]:
A2C_PARAMS = {"n_steps": 5, "ent_coef": 0.005, "learning_rate": 0.0002}
model_a2c = agent_multipleticker.get_model(model_name="a2c",model_kwargs = A2C_PARAMS, tensorboard_log = config.TENSORBOARD_LOG_DIR)

Using cuda device


In [17]:
trained_a2c = agent_multipleticker.train_model(model=model_a2c, 
                                tb_log_name='a2c',
                                total_timesteps=10000)

Logging to ./tensorboard_log_from_main\a2c_1
------------------------------------
| time/                 |          |
|    fps                | 16       |
|    iterations         | 100      |
|    time_elapsed       | 30       |
|    total_timesteps    | 500      |
| train/                |          |
|    entropy_loss       | -11.4    |
|    explained_variance | -15.3    |
|    learning_rate      | 0.0002   |
|    n_updates          | 99       |
|    policy_loss        | -1.93    |
|    std                | 1        |
|    value_loss         | 0.105    |
------------------------------------
------------------------------------
| time/                 |          |
|    fps                | 18       |
|    iterations         | 200      |
|    time_elapsed       | 54       |
|    total_timesteps    | 1000     |
| train/                |          |
|    entropy_loss       | -11.4    |
|    explained_variance | -290     |
|    learning_rate      | 0.0002   |
|    n_updates          | 199 

### Model 3: **PPO**

In [18]:
# agent = DRLAgent(env = env_train)
# PPO_PARAMS = {
#     "n_steps": 2048,
#     "ent_coef": 0.005,
#     "learning_rate": 0.0001,
#     "batch_size": 128,
# }
# model_ppo = agent.get_model("ppo",model_kwargs = PPO_PARAMS)

In [19]:
# trained_ppo = agent.train_model(model=model_ppo, 
#                              tb_log_name='ppo',
#                              total_timesteps=80000)

## Trading
Assume that we have $1,000,000 initial capital at 2021-01-01.

In [20]:
trade_dqn = data_split(df,config.START_TEST_DATE, config.END_DATE)
e_trade_gym_dqn = CustomTradingEnv(df = trade_dqn, **env_kwargs_singleticker)

In [21]:
trade_a2c = data_split(df,config.START_TEST_DATE, config.END_DATE)
e_trade_gym_a2c = CustomTradingEnv(df = trade_a2c, **env_kwargs_multipleticker)

In [22]:
trade_dqn.shape

(34752, 82)

In [23]:
trade_a2c.shape

(34752, 82)

In [24]:
trade_dqn

date          open          high           low  \
0    2021-01-01 00:00:00      0.181340      0.181460      0.178310   
0    2021-01-01 00:00:00     37.359600     37.442300     36.963600   
0    2021-01-01 00:00:00  28923.630000  29031.340000  28690.170000   
0    2021-01-01 00:00:00      0.004672      0.004701      0.004601   
0    2021-01-01 00:00:00    736.420000    739.000000    729.330000   
...                  ...           ...           ...           ...   
4343 2021-06-30 23:00:00      0.253750      0.255120      0.251920   
4343 2021-06-30 23:00:00   2257.300000   2281.920000   2255.320000   
4343 2021-06-30 23:00:00     19.333000     19.574000     19.318000   
4343 2021-06-30 23:00:00    143.510000    144.620000    143.130000   
4343 2021-06-30 23:00:00      0.690600      0.706900      0.689100   

             close        volume   tic  psar        ui         atr  ...  \
0         0.180510  1.919492e+07   ada   0.0  3.174316    0.003072  ...   
0        37.376400  9.511383e+04   bnb   1.0  2.328882    0.404216  ...   
0     28995.130000  2.311811e+03   btc   0.0  1.505422  378.624288  ...   
0         0.004679  2.768207e+07  doge   0.0  2.016111    0.000074  ...   
0       734.070000  2.793270e+04   eth   0.0  1.998452    9.626878  ...   
...            ...           ...   ...   ...       ...         ...  ...   
4343      0.253910  3.729461e+07  doge   0.0  4.220380    0.005068  ...   
4343   2275.680000  3.543225e+04   eth   0.0  1.657382   40.438589  ...   
4343     19.516000  1.813782e+05  link   0.0  3.388434    0.387212  ...   
4343    144.260000  1.647400e+04   ltc   0.0  2.968342    2.205526  ...   
4343      0.706300  2.075675e+07   xrp   0.0  4.017930    0.013702  ...   

       cov_4_4   cov_4_5   cov_4_6   cov_4_7   cov_5_5   cov_5_6   cov_5_7  \
0     0.000069  0.000071  0.000066  0.000068  0.000204  0.000079  0.000089   
0     0.000069  0.000071  0.000066  0.000068  0.000204  0.000079  0.000089   
0     0.000069  0.000071  0.000066  0.000068  0.000204  0.000079  0.000089   
0     0.000069  0.000071  0.000066  0.000068  0.000204  0.000079  0.000089   
0     0.000069  0.000071  0.000066  0.000068  0.000204  0.000079  0.000089   
...        ...       ...       ...       ...       ...       ...       ...   
4343  0.000200  0.000205  0.000185  0.000164  0.000317  0.000227  0.000209   
4343  0.000200  0.000205  0.000185  0.000164  0.000317  0.000227  0.000209   
4343  0.000200  0.000205  0.000185  0.000164  0.000317  0.000227  0.000209   
4343  0.000200  0.000205  0.000185  0.000164  0.000317  0.000227  0.000209   
4343  0.000200  0.000205  0.000185  0.000164  0.000317  0.000227  0.000209   

       cov_6_6   cov_6_7   cov_7_7  
0     0.000110  0.000091  0.000217  
0     0.000110  0.000091  0.000217  
0     0.000110  0.000091  0.000217  
0     0.000110  0.000091  0.000217  
0     0.000110  0.000091  0.000217  
...        ...       ...       ...  
4343  0.000266  0.000202  0.000412  
4343  0.000266  0.000202  0.000412  
4343  0.000266  0.000202  0.000412  
4343  0.000266  0.000202  0.000412  
4343  0.000266  0.000202  0.000412  

[34752 rows x 82 columns]

In [25]:
trade_a2c

date          open          high           low  \
0    2021-01-01 00:00:00      0.181340      0.181460      0.178310   
0    2021-01-01 00:00:00     37.359600     37.442300     36.963600   
0    2021-01-01 00:00:00  28923.630000  29031.340000  28690.170000   
0    2021-01-01 00:00:00      0.004672      0.004701      0.004601   
0    2021-01-01 00:00:00    736.420000    739.000000    729.330000   
...                  ...           ...           ...           ...   
4343 2021-06-30 23:00:00      0.253750      0.255120      0.251920   
4343 2021-06-30 23:00:00   2257.300000   2281.920000   2255.320000   
4343 2021-06-30 23:00:00     19.333000     19.574000     19.318000   
4343 2021-06-30 23:00:00    143.510000    144.620000    143.130000   
4343 2021-06-30 23:00:00      0.690600      0.706900      0.689100   

             close        volume   tic  psar        ui         atr  ...  \
0         0.180510  1.919492e+07   ada   0.0  3.174316    0.003072  ...   
0        37.376400  9.511383e+04   bnb   1.0  2.328882    0.404216  ...   
0     28995.130000  2.311811e+03   btc   0.0  1.505422  378.624288  ...   
0         0.004679  2.768207e+07  doge   0.0  2.016111    0.000074  ...   
0       734.070000  2.793270e+04   eth   0.0  1.998452    9.626878  ...   
...            ...           ...   ...   ...       ...         ...  ...   
4343      0.253910  3.729461e+07  doge   0.0  4.220380    0.005068  ...   
4343   2275.680000  3.543225e+04   eth   0.0  1.657382   40.438589  ...   
4343     19.516000  1.813782e+05  link   0.0  3.388434    0.387212  ...   
4343    144.260000  1.647400e+04   ltc   0.0  2.968342    2.205526  ...   
4343      0.706300  2.075675e+07   xrp   0.0  4.017930    0.013702  ...   

       cov_4_4   cov_4_5   cov_4_6   cov_4_7   cov_5_5   cov_5_6   cov_5_7  \
0     0.000069  0.000071  0.000066  0.000068  0.000204  0.000079  0.000089   
0     0.000069  0.000071  0.000066  0.000068  0.000204  0.000079  0.000089   
0     0.000069  0.000071  0.000066  0.000068  0.000204  0.000079  0.000089   
0     0.000069  0.000071  0.000066  0.000068  0.000204  0.000079  0.000089   
0     0.000069  0.000071  0.000066  0.000068  0.000204  0.000079  0.000089   
...        ...       ...       ...       ...       ...       ...       ...   
4343  0.000200  0.000205  0.000185  0.000164  0.000317  0.000227  0.000209   
4343  0.000200  0.000205  0.000185  0.000164  0.000317  0.000227  0.000209   
4343  0.000200  0.000205  0.000185  0.000164  0.000317  0.000227  0.000209   
4343  0.000200  0.000205  0.000185  0.000164  0.000317  0.000227  0.000209   
4343  0.000200  0.000205  0.000185  0.000164  0.000317  0.000227  0.000209   

       cov_6_6   cov_6_7   cov_7_7  
0     0.000110  0.000091  0.000217  
0     0.000110  0.000091  0.000217  
0     0.000110  0.000091  0.000217  
0     0.000110  0.000091  0.000217  
0     0.000110  0.000091  0.000217  
...        ...       ...       ...  
4343  0.000266  0.000202  0.000412  
4343  0.000266  0.000202  0.000412  
4343  0.000266  0.000202  0.000412  
4343  0.000266  0.000202  0.000412  
4343  0.000266  0.000202  0.000412  

[34752 rows x 82 columns]

In [26]:
allocations_dqn, transactions_dqn, allocation_values_dqn = agent_singleticker.DRL_prediction(model=trained_dqn,
                        environment = e_trade_gym_dqn)

hit end!


In [27]:
allocations_dqn

cash   btc                date
0   11266.067  31.0 2021-01-01 01:00:00
0   11266.067  31.0 2021-01-01 02:00:00
0   11266.067  31.0 2021-01-01 03:00:00
0   11266.067  31.0 2021-01-01 04:00:00
0   11266.067  31.0 2021-01-01 05:00:00
..        ...   ...                 ...
0   29517.874   0.0 2021-06-30 17:00:00
0   29517.874   0.0 2021-06-30 18:00:00
0   29517.874   0.0 2021-06-30 19:00:00
0   29517.874   0.0 2021-06-30 20:00:00
0   29517.874   0.0 2021-06-30 21:00:00

[4341 rows x 3 columns]

In [28]:
transactions_dqn

date operation  tic  amount     price
0 2021-01-01 00:00:00       buy  btc    31.0  28995.13
0 2021-01-02 23:00:00      sell  btc    31.0  32178.33
0 2021-01-03 01:00:00       buy  btc    25.0  32585.09
0 2021-01-03 03:00:00      sell  btc    25.0  32573.87
0 2021-01-03 05:00:00       buy  btc    19.0  33758.67
0 2021-01-03 06:00:00       buy  btc     1.0  33967.13
0 2021-01-03 08:00:00      sell  btc    20.0  34367.68
0 2021-01-03 09:00:00       buy  btc    16.0  34190.55
0 2021-01-04 04:00:00      sell  btc    16.0  33257.55
0 2021-01-04 05:00:00       buy  btc    13.0  32813.01
0 2021-01-05 10:00:00      sell  btc    13.0  31345.77
0 2021-01-05 11:00:00       buy  btc    11.0  31776.66
0 2021-01-05 16:00:00      sell  btc    11.0  32469.90
0 2021-01-05 17:00:00       buy  btc     9.0  32742.73
0 2021-01-06 11:00:00      sell  btc     9.0  34918.53
0 2021-01-06 12:00:00       buy  btc     7.0  34929.87
0 2021-01-06 20:00:00      sell  btc     7.0  36015.88
0 2021-01-06 21:00:00       buy  btc     6.0  35874.16
0 2021-01-10 03:00:00      sell  btc     6.0  40316.64
0 2021-01-10 04:00:00       buy  btc     5.0  40342.46
0 2021-01-11 20:00:00      sell  btc     5.0  33409.80
0 2021-01-11 21:00:00       buy  btc     4.0  33968.09
0 2021-01-14 04:00:00      sell  btc     4.0  37504.00
0 2021-01-14 05:00:00       buy  btc     3.0  37529.11
0 2021-01-14 06:00:00      sell  btc     3.0  37837.21
0 2021-01-14 07:00:00       buy  btc     2.0  38198.34
0 2021-01-14 09:00:00      sell  btc     2.0  37938.11
0 2021-01-14 13:00:00       buy  btc     2.0  38977.66
0 2021-01-16 16:00:00      sell  btc     2.0  37231.41
0 2021-01-16 19:00:00       buy  btc     2.0  36376.39
0 2021-01-16 21:00:00      sell  btc     2.0  35924.44
0 2021-01-16 22:00:00       buy  btc     1.0  36121.12
0 2021-01-17 02:00:00      sell  btc     1.0  36419.68
0 2021-01-17 03:00:00       buy  btc     1.0  36177.00
0 2021-01-17 04:00:00      sell  btc     1.0  35847.46
0 2021-01-17 05:00:00       buy  btc     1.0  35547.13
0 2021-01-17 06:00:00      sell  btc     1.0  35390.80
0 2021-01-17 07:00:00       buy  btc     1.0  34760.90
0 2021-01-17 17:00:00      sell  btc     1.0  35837.22
0 2021-01-17 18:00:00       buy  btc     1.0  35678.67
0 2021-01-19 02:00:00      sell  btc     1.0  36804.11
0 2021-01-20 03:00:00       buy  btc     1.0  35062.49
0 2021-01-24 00:00:00      sell  btc     1.0  31876.35

In [29]:
allocation_values_dqn

cash        btc                date
0   11266.067  911709.69 2021-01-01 01:00:00
0   11266.067  905034.15 2021-01-01 02:00:00
0   11266.067  907630.40 2021-01-01 03:00:00
0   11266.067  905829.61 2021-01-01 04:00:00
0   11266.067  904797.31 2021-01-01 05:00:00
..        ...        ...                 ...
0   29517.874       0.00 2021-06-30 17:00:00
0   29517.874       0.00 2021-06-30 18:00:00
0   29517.874       0.00 2021-06-30 19:00:00
0   29517.874       0.00 2021-06-30 20:00:00
0   29517.874       0.00 2021-06-30 21:00:00

[4341 rows x 3 columns]

In [30]:
allocations_a2c, transactions_a2c, allocation_values_a2c = agent_multipleticker.DRL_prediction(model=trained_a2c,
                        environment = e_trade_gym_a2c)

hit end!


In [31]:
allocations_a2c

cash          ada          bnb   btc         doge        eth  \
0   983209.117747   100.000000     0.000000   0.0     0.000000  13.556287   
0   976532.033330   130.430982    65.287572   0.0     0.000000   0.000000   
0   929783.131898   230.430982   165.287572   0.0    25.817430  64.038289   
0    12697.302209   186.330670   126.277220  31.0     0.000000  83.038289   
0       81.131355   268.539894   172.441867  31.0   100.000000  97.038289   
..            ...          ...          ...   ...          ...        ...   
0     1942.807257  3697.845195  3859.312662   4.0  5365.783126   0.000000   
0       61.755693  3597.845195  3866.312662   4.0  5340.099190   0.000000   
0    12781.945508  3602.026166  3866.312662   4.0  5412.716828   0.000000   
0       82.661061  3589.891472  3908.312662   4.0  5512.716828   0.000000   
0    43461.477781  3630.259227  3808.312662   4.0  5525.344468   0.000000   

          link         ltc          xrp                date  
0   100.000000   44.442073   100.000000 2021-01-01 01:00:00  
0   182.334799  144.442073     0.000000 2021-01-01 02:00:00  
0   262.364542   97.570258   100.000000 2021-01-01 03:00:00  
0   284.364542    0.000000   191.091239 2021-01-01 04:00:00  
0   184.364542   11.000000   270.557016 2021-01-01 05:00:00  
..         ...         ...          ...                 ...  
0     0.000000  708.186732  6387.651478 2021-06-30 17:00:00  
0     2.000000  708.186732  6294.407879 2021-06-30 18:00:00  
0     0.000000  617.376594  6220.851915 2021-06-30 19:00:00  
0     0.000000  618.376594  6138.198166 2021-06-30 20:00:00  
0     0.000000  518.376594  6167.275702 2021-06-30 21:00:00  

[4341 rows x 10 columns]

In [32]:
transactions_a2c

date operation   tic      amount      price
0  2021-01-01 00:00:00       buy   ada  100.000000    0.18051
0  2021-01-01 00:00:00       buy   eth   13.556287  734.07000
0  2021-01-01 00:00:00       buy  link  100.000000   11.28120
0  2021-01-01 00:00:00       buy   ltc   44.442073  123.87000
0  2021-01-01 00:00:00       buy   xrp  100.000000    0.22162
..                 ...       ...   ...         ...        ...
0  2021-06-30 20:00:00       buy   ada   40.367755    1.37030
0  2021-06-30 20:00:00      sell   bnb  100.000000  296.81000
0  2021-06-30 20:00:00       buy  doge   12.627640    0.25140
0  2021-06-30 20:00:00      sell   ltc  100.000000  142.16000
0  2021-06-30 20:00:00       buy   xrp   29.077536    0.68570

[25823 rows x 5 columns]

In [33]:
allocation_values_a2c

cash          ada           bnb        btc         doge  \
0   983209.117747    18.358000  0.000000e+00       0.00     0.000000   
0   976532.033330    23.957563  2.478316e+03       0.00     0.000000   
0   929783.131898    42.150435  6.268531e+03       0.00     0.128522   
0    12697.302209    33.874916  4.782144e+03  905829.61     0.000000   
0       81.131355    49.134744  6.503283e+03  904797.31     0.494190   
..            ...          ...           ...        ...          ...   
0     1942.807257  4935.513981  1.115226e+06  138829.40  1334.845868   
0       61.755693  4890.191189  1.134105e+06  139287.96  1347.894436   
0    12781.945508  5004.294953  1.148720e+06  138974.24  1368.280687   
0       82.661061  4919.228284  1.160026e+06  138321.60  1385.897011   
0    43461.477781  4990.154334  1.139485e+06  139224.64  1382.441186   

             eth         link           ltc          xrp                date  
0   10143.898206  1147.350000   5853.020950    22.382000 2021-01-01 01:00:00  
0       0.000000  2110.944664  19258.461528     0.000000 2021-01-01 02:00:00  
0   47696.998110  3017.349657  12846.100218    22.730000 2021-01-01 03:00:00  
0   61638.491240  3258.106746      0.000000    45.666984 2021-01-01 04:00:00  
0   71871.408447  2109.701896   1439.680000    64.443976 2021-01-01 05:00:00  
..           ...          ...           ...          ...                 ...  
0       0.000000     0.000000  98636.247991  4255.453415 2021-06-30 17:00:00  
0       0.000000    38.276000  99705.609955  4256.278608 2021-06-30 18:00:00  
0       0.000000     0.000000  87389.656840  4251.952284 2021-06-30 19:00:00  
0       0.000000     0.000000  87908.416562  4208.962483 2021-06-30 20:00:00  
0       0.000000     0.000000  74257.447049  4256.036962 2021-06-30 21:00:00  

[4341 rows x 10 columns]

<a id='6'></a>
# Part 7: Backtest

In [34]:
%load_ext autoreload
%autoreload 
bat_dqn = BackTest(trained_dqn, e_trade_gym_dqn)
bat_dqn.create_summary(allocations_dqn, allocation_values_dqn, transactions_dqn)

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [35]:
bat_dqn.plot_return_against_hold(allocation_values_dqn)

In [36]:
%load_ext autoreload
%autoreload 
bat_a2c = BackTest(trained_a2c, e_trade_gym_a2c)
bat_a2c.create_summary(allocations_a2c, allocation_values_a2c, transactions_a2c)

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [37]:
bat_a2c.plot_return_against_hold(allocation_values_a2c)

In [38]:
%load_ext autoreload
%autoreload 
from trade.time_series_validation import TimeSeriesValidation
tsv = TimeSeriesValidation(num_splits=5, total_timesteps_model=1000, with_graphs=False)

model_name = "a2c"
model_params = {"n_steps": 5, "ent_coef": 0.005, "learning_rate": 0.0002}

stock_dimension = len(df.tic.unique())
state_space = stock_dimension
features = config.TECHNICAL_INDICATORS_LIST + ["open", "close", 'high', 'low']
features += [f"{feature}_diff" for feature in features]
features += [feature for feature in df.columns if feature.startswith("cov_")]

env_params = {
    "initial_amount": 1000000, 
    "technical_indicator_list": features, 
    "max_assets_amount_per_trade": 100, 
    "main_tickers": df.tic.unique(),
    "all_tickers": df.tic.unique(),
    "reward_scaling": 1e-4,
    "comission_value": 0.01
    
}


results = tsv.run(df, env_params, model_name, model_params)

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload
Train from [2020-06-29 00:00:00] to [2020-08-23 00:00:00]
Using cuda device
------------------------------------
| time/                 |          |
|    fps                | 28       |
|    iterations         | 100      |
|    time_elapsed       | 17       |
|    total_timesteps    | 500      |
| train/                |          |
|    entropy_loss       | -11.4    |
|    explained_variance | -1.24    |
|    learning_rate      | 0.0002   |
|    n_updates          | 99       |
|    policy_loss        | 0.22     |
|    std                | 1        |
|    value_loss         | 0.0187   |
------------------------------------
------------------------------------
| time/                 |          |
|    fps                | 29       |
|    iterations         | 200      |
|    time_elapsed       | 33       |
|    total_timesteps    | 1000     |
| train/                |          |
|    entropy_loss     

In [39]:
results

{'return': -0.685059318568451,
 'sharpe': -87.11496694720941,
 'sortino': -120.89051400609382,
 'max_drawdown': -0.6858325086550184}